## Setting up the environment
Use interpreter = 'Python 3.8.8 64-bit ('base': conda)'



In [2]:
import streamlit as st

In [3]:
import pandas as pd
import pandas_profiling
from pandas_profiling import ProfileReport
import numpy as np
import plotly 
import plotly.express as px 
from scipy import stats  # for removing outliers

2021-11-15 22:03:44.098 INFO    visions.backends: Pandas backend loaded 1.2.4
2021-11-15 22:03:44.104 INFO    visions.backends: Numpy backend loaded 1.20.1
2021-11-15 22:03:44.104 INFO    visions.backends: Pyspark backend NOT loaded
2021-11-15 22:03:44.105 INFO    visions.backends: Python backend loaded


### Read in the source data.

In [4]:
#df = pd.read_csv('data/thor_17.csv', parse_dates = ['DATA_DATE'])
df = pd.read_csv('data/thor_17.csv', index_col='DATA_DATE', parse_dates=True)
#df.info()
#df.describe()
df.head()

POOL_NAME  POOL_DEPTH_USD  N_UNIQUE_LPERS  \
DATA_DATE                                                                 
2021-04-11 00:00:00+00:00       BCH.BCH   171797.837764               3   
2021-04-11 00:00:00+00:00       BNB.BNB   467835.604144               3   
2021-04-11 00:00:00+00:00  BNB.BUSD-BD1   428809.697648               3   
2021-04-11 00:00:00+00:00       BTC.BTC   408839.638798               3   
2021-04-11 00:00:00+00:00       ETH.ETH   557234.146326               3   

                           N_UNIQUE_PROVIDERS  N_UNIQUE_TAKERAWAYERS  
DATA_DATE                                                             
2021-04-11 00:00:00+00:00                   3                      0  
2021-04-11 00:00:00+00:00                   3                      0  
2021-04-11 00:00:00+00:00                   3                      0  
2021-04-11 00:00:00+00:00                   3                      0  
2021-04-11 00:00:00+00:00                   3                      0

### Extract `chain` and `asset` info from `pool_name`.

In [33]:
df[['CHAIN', 'ASSET']]    = df['POOL_NAME'].str.split('.', 1, expand=True)
df[['ASSET', 'ALT_INFO']] = df['ASSET'].str.split('-', 1, expand=True)
df.head()

POOL_NAME  POOL_DEPTH_USD  N_UNIQUE_LPERS  \
DATA_DATE                                                                 
2021-04-11 00:00:00+00:00       BCH.BCH   171797.837764               3   
2021-04-11 00:00:00+00:00       BNB.BNB   467835.604144               3   
2021-04-11 00:00:00+00:00  BNB.BUSD-BD1   428809.697648               3   
2021-04-11 00:00:00+00:00       BTC.BTC   408839.638798               3   
2021-04-11 00:00:00+00:00       ETH.ETH   557234.146326               3   

                           N_UNIQUE_PROVIDERS  N_UNIQUE_TAKERAWAYERS CHAIN  \
DATA_DATE                                                                    
2021-04-11 00:00:00+00:00                   3                      0   BCH   
2021-04-11 00:00:00+00:00                   3                      0   BNB   
2021-04-11 00:00:00+00:00                   3                      0   BNB   
2021-04-11 00:00:00+00:00                   3                      0   BTC   
2021-04-11 00:00:00+00:00                   3                      0   ETH   

                          ASSET ALT_INFO  
DATA_DATE                                 
2021-04-11 00:00:00+00:00   BCH     None  
2021-04-11 00:00:00+00:00   BNB     None  
2021-04-11 00:00:00+00:00  BUSD      BD1  
2021-04-11 00:00:00+00:00   BTC     None  
2021-04-11 00:00:00+00:00   ETH     None

In [37]:
np.sort(df.ASSET.unique())

array(['AAVE', 'ADA', 'ALCX', 'ALPHA', 'AVA', 'BCH', 'BNB', 'BTC', 'BTCB',
       'BUSD', 'CAS', 'CREAM', 'DNA', 'DODO', 'DOT', 'ETH', 'ETHBULL',
       'FOX', 'FRM', 'FTM', 'HEGIC', 'HOT', 'KYL', 'LINK', 'LTC', 'NEXO',
       'PERP', 'RAZE', 'SNX', 'SUSHI', 'THOR', 'TVK', 'TWT', 'USDC',
       'USDT', 'WBTC', 'XRP', 'XRUNE', 'YFI'], dtype=object)

In [24]:
fig = px.scatter(df, x=df.index, y='POOL_DEPTH_USD', color='ASSET', facet_col='CHAIN', facet_col_wrap=2)
fig.show()
#fig.write_image('images/by_chain.png')

In [6]:
no_outliers = df[(np.abs(stats.zscore(df['RUNE_VOLUME'])) < 3)]
df.describe()
no_outliers.describe()

DATA_HOUR   RUNE_VOLUME    RUNE_PRICE
count  25428.000000  25428.000000  25428.000000
mean      11.515731   3692.396132     10.214793
std        6.823776   6961.415295      3.795641
min        0.000000      0.022369      4.659394
25%        6.000000    303.837864      7.211110
50%       12.000000    970.001165      8.947293
75%       17.000000   3434.793380     12.693235
max       23.000000  48862.783397     20.503791

In [26]:
fig = px.scatter(no_outliers, x='DATA_DATE', y='RUNE_PRICE', color='RUNE_VOLUME', opacity=.027, height=400, width=800)
fig.show()
fig.write_image('images/date_v_price.png')

In [21]:
fig = px.scatter(no_outliers, 
                 x='RUNE_VOLUME', 
                 y='RUNE_PRICE', 
                 trendline='ols', 
                 trendline_color_override='red',
                 marginal_x='histogram', 
                 marginal_y='histogram',
                 opacity=.15,
                 height=400, 
                 width=800)
fig.show()
fig.write_image('images/volume_v_price.png')

In [14]:
results = px.get_trendline_results(fig)
results

px_fit_results
0  <statsmodels.regression.linear_model.Regressio...